In [ ]:
import numpy as np
import netCDF4 as nc
import xarray as xr
import matplotlib.pyplot as pl
import math
import scipy.io as sc
import netCDF4 as nc
import os, glob
import matplotlib.animation as manimation
from IPython.display import HTML
from matplotlib import rc
from matplotlib import cm
import matplotlib
import sys
#matplotlib.use('TKAgg')

def make_netcdffile_fromcross(time_start, time_end, time_gap, x_spacing, path, output_name, del_files): #output netcdf file with variable across time steps from dump files
    float_type = 'f8'
    time_ind_total = int((time_end-time_start)/time_gap) + 1
    time = np.linspace(time_start,time_end,time_ind_total)
    main_variable=['qr','ql','couvreux','bc']
    attribute=['path','up','base']
    cross_section='.xy.'
    cross_section_length = 90
    filename = path+main_variable[0] + attribute[0] + cross_section + str(format(int(time[0]),'07d'))
    fid=open(filename,'rb')
    x_length = int(np.sqrt(len(np.fromfile(fid))))
    x=np.linspace(x_spacing,x_length*x_spacing,x_length)
    y=np.linspace(x_spacing,x_length*x_spacing,x_length)
    nvar=3
    fid.close()
    if os.path.exists(path+output_name):
        os.remove(path+output_name)
    nc_file = nc.Dataset(path+output_name, mode="w", datamodel="NETCDF4", clobber=False)
    nc_file.createDimension("x", x_length)
    nc_file.createDimension("y", x_length)
    nc_file.createDimension("t", time_ind_total)
    nc_file.createDimension("nvar",nvar)
    nc_x = nc_file.createVariable("x", float_type, ("x"))
    nc_y = nc_file.createVariable("y", float_type, ("y"))
    nc_t = nc_file.createVariable("t", float_type, ("t"))
    nc_nvar = nc_file.createVariable("nvar", int, ("nvar"))

    for j in range(0,len(main_variable)-1):
        var_name = main_variable[j]
        locals()[var_name] = np.zeros((x_length,x_length,time_ind_total,nvar))
        locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t","nvar"))  
        for k in range(0,len(attribute)):                  
            for i in range(0,time_ind_total):
                filename = path+main_variable[j] + attribute[k] + cross_section + str(format(int(time[i]),'07d'))
                fid=open(filename,'rb')
                var = np.fromfile(fid)
                locals()[var_name][:,:,i,k]=np.reshape(var,[x_length,x_length])
                fid.close()
        locals()['nc_'+var_name][:] = locals()[var_name][:]
    
    var_name = main_variable[3]
    locals()[var_name] = np.zeros((x_length,x_length,time_ind_total))
    locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t"))                  
    for i in range(0,time_ind_total):
        filename = path+main_variable[3] +attribute[0]+ cross_section + str(format(int(time[i]),'07d'))
        fid=open(filename,'rb')
        var = np.fromfile(fid)
        locals()[var_name][:,:,i]=np.reshape(var,[x_length,x_length])
        fid.close()
    locals()['nc_'+var_name][:] = locals()[var_name][:]




    nc_x [:] = x[:]
    nc_y [:] = y[:]
    nc_t [:] = time[:]
    nc_nvar [:]=nvar 
    nc_file.close()
    if del_files:
        #files = ["u", "v", "w", "thl", "time", "qr", "ql", "couv", "grid", "nr","qt","therm","bc"]
        files = ["path","up","base"]
        for file in os.listdir(path):
            for i in range(0,len(files)):
                if file.find(files[i])!=-1: 
                    os.remove(path+file)
                #rm u* v* w* thl* time* qr* ql* couv* grid* nr* qt* therm* 
##########################################################################################
def retrieve_variable(variable_name,netcdf_path): #open corresponding netcdf file and read data
    all_data=xr.open_dataset(netcdf_path)
    var=all_data[variable_name].values
    x=all_data['x'].values
    y=all_data['y'].values
    t=all_data['t'].values
    return var, x, y, t;    
##########################################################################################
def find_boolean(variable, threshold_criteria, i_tstart): #variable is f(i, j, t): --> outputs boolean -1 (unsatisfied) 0 (satisfied) 
    boolean = np.zeros(( len(variable[:,0,0]), len(variable[0,:,0]), len(variable[0,0,:])))
    boolean = -1
    boolean = np.where(variable>threshold_criteria,0,-1)
    if i_tstart>0:
        boolean[:,:,0:i_tstart-1] = -1
    return boolean;
##########################################################################################
class cell:
    def __init__(self, id):
        self.id = id
        self.value = [[],[],[]]
        self.location = [[],[],[]]
        self.nelements = 0
        self.nchildren = 0
        self.nparents = 0
        self.nsiblings = 0
        self.nsplitters = 0
        self.parents = []
        self.children = []

    def add_elements(self, i, j, k, var_values):
        self.location[0].append(i)
        self.location[1].append(j)
        self.location[2].append(k)
        self.value[0].append(var_values[0])
        self.value[1].append(var_values[1])
        self.value[2].append(var_values[2])
        self.nelements = self.nelements + 1
########################################################################################
def identify_elements_in_cell(boolean,variable,i,j,k,new_cell):  #input the ijk at which boolean is satisfied along with boolean and new cell created 
    nx = len(variable[:,0,0,0])                                  # outputs the cell with with added elements in it (location and value of it)
    ny = len(variable[0,:,0,0])
    nt = len(variable[0,0,:,0])
    ipath=0; iup=1; ibase=2;
    new_cell.add_elements(i,j,k,variable[i,j,k,:])
    boolean[i,j,k] = -2

    ii=i-1; jj=j; kk=k; #look west
    if ii<0:
        ii = nx-1
    if (boolean[ii,jj,kk] == 0) and \
    ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
    and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(boolean,variable,ii,jj,kk,new_cell)

    ii=i+1; jj=j; kk=k;  #look east
    if ii>nx-1:
        ii = 0
    if (boolean[ii,jj,kk] == 0) and \
    ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
    and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(boolean,variable,ii,jj,kk,new_cell)

    ii=i; jj=j+1; kk=k;  #look north
    if jj>ny-1:
        jj = 0
    if (boolean[ii,jj,kk] == 0) and \
    ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
    and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(boolean,variable,ii,jj,kk,new_cell)

    ii=i; jj=j-1; kk=k;  #look south
    if jj<0:
        jj = ny-1
    if (boolean[ii,jj,kk] == 0) and \
    ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
    and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
        new_cell.add_elements(ii,jj,kk,variable[ii,jj,kk,:])
        identify_elements_in_cell(boolean,variable,ii,jj,kk,new_cell)

    ii=i; jj=j; kk=min(k+1,nt-1);  #look forward
    if (boolean[ii,jj,kk] == 0) and \
    ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
    and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(boolean,variable,ii,jj,kk,new_cell)

    ii=i; jj=j; kk=max(k-1,0);  #look backward
    if (boolean[ii,jj,kk] == 0) and \
    ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
    and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(boolean,variable,ii,jj,kk,new_cell)
    return boolean;
#################################################################################################
def create_new_cell(variable, bool):                                # input the boolean and the variable, output is the cells tracked (i,j,t) based on boolean 
    nx = len(variable[:,0,0,0])
    ny = len(variable[0,:,0,0])
    nt = len(variable[0,0,:,0])
    cell_number = 0
    variable_cells = []
    for i in range(0,nx):
        for j in range(0,ny):
            for k in range(0,nt):
                if bool[i,j,k]==0:
                    variable_cells.append(cell(cell_number))
                    bool=identify_elements_in_cell(bool,variable,i,j,k,variable_cells[cell_number])
                    variable_cells[cell_number].id = cell_number
                    cell_number = cell_number + 1
    return variable_cells, cell_number;
##################################################################################################
def fill_parent_array(cells,nx,ny,nt):                                     #fills parent_array variable with id numbers of cells corresponding to each grid point 
    parent_array=np.zeros((nx,ny,nt))                             # fills base and up with values of base and up at those grid points
    base=np.zeros((nx,ny,nt))
    up=np.zeros((nx,ny,nt))
    for c in range(0,len(cells)):
        for n in range(0,cells[c].nelements):
            parent_array[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].id + 1
            base[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[ibase][n]
            up[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[iup][n]
    return parent_array,base,up;
#################################################################################################
def find_parent(cells,parent_cells,parent_array,base,up):
    lnewparent=False
    for n in range(0,len(cells)):
        for nn in range(0,cells[n].nelements):
            i = cells[n].location[0][nn]
            j = cells[n].location[1][nn]
            t = cells[n].location[2][nn]
            if parent_array[i,j,t] > 0:
                if base[i,j,t] <= cells[n].value[iup][cells[n].nelements-1] and up[i,j,t] >= cells[n].value[ibase][cells[n].nelements-1]:
                    lnewparent = True
                    for np in range(0,cells[n].nparents):
                        if cells[n].nparents>0 and (cells[n].parents[np].id == parent_array[i,j,t]-1):
                            lnewparent=False
                    if lnewparent:
                        cells[n].parents.append(parent_cells[int(parent_array[i,j,t]-1)])
                        parent_cells[int(parent_array[i,j,t]-1)].children.append(cells[n])                       
                        cells[n].nparents = cells[n].nparents + 1
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren = \
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren + 1
    return cells,parent_cells;
#################################################################################################
def splitcell(cells, parent_cells, parent_array):
    a=0
#################################################################################################
def run_tracking(tracked_param,nc_path,nc_filename,param_threshold,t_start):
    [tracked_variable,x,y,t] = retrieve_variable(tracked_param,nc_path+nc_filename);
    bool = find_boolean(tracked_variable[:,:,:,ipath],param_threshold,t_start)
    [cells,cell_number] = create_new_cell(tracked_variable,bool);
    return cells,cell_number,tracked_variable,x,y,t,bool;
##################################################################################################
def make_contourplot(x,y,plot_variable,title,xlabel,ylabel):
    pl.figure()
    pl.contour(x,y,plot_variable)
    pl.title(title)
    pl.xlabel(xlabel)
    pl.ylabel(ylabel)
    if np.sum(plot_variable)>0:
        pl.colorbar()
    pl.show() 
###################################################################################################
def get_contour_fromcell(cells,output_contour,output_parent_contour):
    for i in range(0,len(cells)):
        for n in range(0,cells[i].nelements):
            output_contour[cells[i].location[0][n],cells[i].location[1][n],cells[i].location[2][n]] = cells[i].value[0][n]
        if cells[i].nparents>0:
            for npar in range(0,cells[i].nparents):
                for n in range(0,cells[i].parents[npar].nelements):    
                    output_parent_contour[cells[i].parents[npar].location[0][n],cells[i].parents[npar].location[1][n],cells[i].parents[npar].location[2][n]]\
                    = cells[i].parents[npar].value[0][n]
    return output_contour,output_parent_contour;
##################################################################################################
def make_3d_plot_animation(cells,nt):
    x_3d = ([]); y_3d=([]); z_3d = ([]);t_3d=[];
    for i in range(0,len(cells)):
        for n in range(0,cells[i].nelements):
            t=cells[i].location[2][n]
            if t==10:
                for z in range(int(cells[i].value[2][n]),int(cells[i].value[1][n])):
                    x_3d.append(cells[i].location[0][n])
                    y_3d.append(cells[i].location[1][n])
                    z_3d.append(z)
    pl.figure()
    ax = pl.axes(projection='3d')
    ax.scatter(x_3d,y_3d,z_3d,marker='o',s=1)

        
    #ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=False)
    pl.show()
    #HTML(ani.to_jshtml())
    #pl.rcParams["animation.html"] = "jshtml"
    #return ani
##################################################################################################    
def make_animation_contour(x,y,variable,nt):
    fig, ax = pl.subplots()
    def animate(i):
        ax.clear()
        CS = ax.contour(x,y,variable[:,:,i])
        ax.clabel(CS, inline=True, fontsize=10)
        return ax;
        
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=False)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
##################################################################################################
def make_animation_cells(x,y,cells,nt,minimum_elements,p_c):
    fig, ax = pl.subplots()
    cell_plot=np.zeros((len(x),len(y),nt));
    cell_parent_plot=np.zeros((len(x),len(y),nt));
    levels=[]
    levels_reduced=[]
    count=0
    for i in range (0,len(cells)):
        if cells[i].nelements>minimum_elements:
            levels.append(i)
            if (count%4)==0:
                levels_reduced.append(i)
            count=count+1
            for n in range(0,cells[i].nelements):      
                    cell_plot[cells[i].location[0][n],cells[i].location[1][n],cells[i].location[2][n]] = cells[i].id
    if p_c=='p':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nparents>0:
                for npar in range(0,cells[i].nparents):
                    for n in range(0,cells[i].parents[npar].nelements):      
                        cell_parent_plot[cells[i].parents[npar].location[0][n],cells[i].parents[npar].location[1][n],(cells[i].parents[npar].location[2][n])] = cells[i].id
    elif p_c=='c':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nchildren>0:
                for nchild in range(0,cells[i].nchildren):
                    for n in range(0,cells[i].children[nchild].nelements):      
                        cell_parent_plot[cells[i].children[nchild].location[0][n],cells[i].children[nchild].location[1][n],(cells[i].children[nchild].location[2][n])] = cells[i].id
    if len(cells)>nmaxcells:
        levels=levels_reduced
    def animate(i):
        ax.clear()
        if p_c=='p':
            ax.contourf(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.tab20b)
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.tab20b,linestyles='solid',linewidth=1.5)
        elif p_c=='c':
            ax.contourf(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.flag)
            ax.contour(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.flag,linestyles='solid')
        elif p_c=='':
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.flag)
        return ax;
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=True)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
##################################################################################################
def main_fun():
    [rain,rain_ncells,rain_variable,x,y,t,rain_boolean]= run_tracking('qr',nc_path,nc_filename,qr_threshold,t_start)
    nx = len(rain_variable[:,0,0,0]); ny = len(rain_variable[0,:,0,0]); nt = len(rain_variable[0,0,:,0]);

    [cloud,cloud_ncells,cloud_path,x,y,t,cloud_boolean] = run_tracking('ql',nc_path,nc_filename,ql_threshold,t_start)
    [parent_array,base,up] = fill_parent_array(cloud,nx,ny,nt)
    [rain,cloud] = find_parent(rain,cloud,parent_array,base,up)
    cell_plot=np.zeros((nx,ny,nt)); cell_parent_plot=np.zeros((nx,ny,nt))
    [cell_plot,cell_parent_plot] = get_contour_fromcell(rain,cell_plot,cell_parent_plot)
    #make_contourplot(x,y,cell_plot[:,:,t_plot],'tracked rain path','x [m]', 'y [m]')

    #make_contourplot(x,y,cell_parent_plot[:,:,t_plot],'parent cloud path','x [m]', 'y [m]')
    #make_contourplot(x,y,rain_variable[:,:,t_plot,0],'actual rain path','x [m]', 'y [m]')
    global ani1,ani2,ani3;
    #make_3d_plot_animation(cloud,nt)
    #ani1 = make_animation_contour(x,y,cell_plot,nt)
    #ani2 = make_animation_contour(x,y,cell_parent_plot,nt)
    #ani3 = make_animation_cells(x,y,rain,nt)
    ani3 = make_animation_cells(x,y,cloud,nt,2,'')
#################################################################################

nc_path='/home/girish/microhh/cases/rico_rgn/rico_moist_moresavefiles/'
nc_filename='cloudtrack_variables.nc'
ipath=0; iup=1; ibase=2
qr_threshold = 0.01; ql_threshold = 0.08; couv_threshold = 0.001; bc_threshold = 0;
t_start = 0; t_plot=7;
sys.setrecursionlimit(20000)

#make_netcdffile_fromcross(25200,28800,60,50,nc_path,nc_filename,True)  
main_fun()
ani3



In [ ]:
import numpy as np
import netCDF4 as nc
import xarray as xr
import matplotlib.pyplot as pl
import math
import scipy.io as sc
import netCDF4 as nc
import os, glob
import matplotlib.animation as manimation
from IPython.display import HTML
from matplotlib import rc
from matplotlib import cm
import sys

def make_netcdffile_fromcross(time_start, time_end, time_gap, x_spacing, path, output_name, del_files): #output netcdf file with variable across time steps from dump files
    float_type = 'f8'
    time_ind_total = int((time_end-time_start)/time_gap) + 1
    time = np.linspace(time_start,time_end,time_ind_total)
    main_variable=['qr','ql','couvreux','bc']
    attribute=['path','up','base']
    cross_section='.xy.'
    cross_section_length = 90
    filename = path+main_variable[0] + attribute[0] + cross_section + str(format(int(time[0]),'07d'))
    fid=open(filename,'rb')
    x_length = int(np.sqrt(len(np.fromfile(fid))))
    x=np.linspace(x_spacing,x_length*x_spacing,x_length)
    y=np.linspace(x_spacing,x_length*x_spacing,x_length)
    nvar=3
    fid.close()
    if os.path.exists(path+output_name):
        os.remove(path+output_name)
    nc_file = nc.Dataset(path+output_name, mode="w", datamodel="NETCDF4", clobber=False)
    nc_file.createDimension("x", x_length)
    nc_file.createDimension("y", x_length)
    nc_file.createDimension("t", time_ind_total)
    nc_file.createDimension("nvar",nvar)
    nc_x = nc_file.createVariable("x", float_type, ("x"))
    nc_y = nc_file.createVariable("y", float_type, ("y"))
    nc_t = nc_file.createVariable("t", float_type, ("t"))
    nc_nvar = nc_file.createVariable("nvar", int, ("nvar"))

    for j in range(0,len(main_variable)-1):
        var_name = main_variable[j]
        locals()[var_name] = np.zeros((x_length,x_length,time_ind_total,nvar))
        locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t","nvar"))  
        for k in range(0,len(attribute)):                  
            for i in range(0,time_ind_total):
                filename = path+main_variable[j] + attribute[k] + cross_section + str(format(int(time[i]),'07d'))
                fid=open(filename,'rb')
                var = np.fromfile(fid)
                locals()[var_name][:,:,i,k]=np.reshape(var,[x_length,x_length])
                fid.close()
        locals()['nc_'+var_name][:] = locals()[var_name][:]
    
    var_name = main_variable[3]
    locals()[var_name] = np.zeros((x_length,x_length,time_ind_total))
    locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t"))                  
    for i in range(0,time_ind_total):
        filename = path+main_variable[3] +attribute[0]+ cross_section + str(format(int(time[i]),'07d'))
        fid=open(filename,'rb')
        var = np.fromfile(fid)
        locals()[var_name][:,:,i]=np.reshape(var,[x_length,x_length])
        fid.close()
    locals()['nc_'+var_name][:] = locals()[var_name][:]




    nc_x [:] = x[:]
    nc_y [:] = y[:]
    nc_t [:] = time[:]
    nc_nvar [:]=nvar 
    nc_file.close()
    if del_files:
        #files = ["u", "v", "w", "thl", "time", "qr", "ql", "couv", "grid", "nr","qt","therm","bc"]
        files = ["path","up","base"]
        for file in os.listdir(path):
            for i in range(0,len(files)):
                if file.find(files[i])!=-1: 
                    os.remove(path+file)
                #rm u* v* w* thl* time* qr* ql* couv* grid* nr* qt* therm* 
##########################################################################################
def retrieve_variable(variable_name,netcdf_path): #open corresponding netcdf file and read data
    all_data=xr.open_dataset(netcdf_path)
    var=all_data[variable_name].values
    if variable_name=='bc':
        variable=np.zeros((len(var[:,0,0]),len(var[0,:,0]),len(var[0,0,:]),3))
        variable[:,:,:,0] = var
    else:
        variable=var
    x=all_data['x'].values
    y=all_data['y'].values
    t=all_data['t'].values
    return variable, x, y, t;    
##########################################################################################
def find_boolean(variable, threshold_criteria, i_tstart): #variable is f(i, j, t): --> outputs boolean -1 (unsatisfied) 0 (satisfied) 
    boolean = np.zeros(( len(variable[:,0,0]), len(variable[0,:,0]), len(variable[0,0,:])))
    boolean = -1
    boolean = np.where(variable>threshold_criteria,0,-1)
    if i_tstart>0:
        boolean[:,:,0:i_tstart-1] = -1
    return boolean;
##########################################################################################
class cell:
    def __init__(self, id):
        self.id = id
        self.value = [[],[],[]]
        self.location = [[],[],[]]
        self.nelements = 0
        self.nelements_local = 0
        self.nchildren = 0
        self.nparents = 0
        self.nsiblings = 0
        self.nsplitters = 0
        self.parents = []
        self.children = []

    def add_elements(self, i, j, k, var_values):
        self.location[0].append(i)
        self.location[1].append(j)
        self.location[2].append(k)
        self.value[0].append(var_values[0])
        self.value[1].append(var_values[1])
        self.value[2].append(var_values[2])
        self.nelements = self.nelements + 1
        self.nelements_local = self.nelements_local + 1
    def __del__(self):
        return
########################################################################################
def identify_elements_in_cell(i,j,k,new_cell):  #input the ijk at which boolean is satisfied along with boolean and new cell created 
    new_cell.add_elements(i,j,k,tracking_variable[i,j,k,:])  
    global oldcell,booli;
    booli[i,j,k] = -2
    oldcell=False      
    

    ii=i-1; jj=j; kk=k; #look west
    if ii<0:
       ii = nx-1
    if (booli[ii,jj,kk] == 0 and not oldcell) and \
       ((tracking_variable[i,j,k,ibase] <= tracking_variable[ii,jj,kk,iup])\
       and (tracking_variable[i,j,k,iup] >= tracking_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i+1; jj=j; kk=k;  #look east
    if ii>nx-1:
        ii = 0
    if (booli[ii,jj,kk] == 0 and not oldcell) and \
      ((tracking_variable[i,j,k,ibase] <= tracking_variable[ii,jj,kk,iup])\
      and (tracking_variable[i,j,k,iup] >= tracking_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j+1; kk=k;  #look north
    if jj>ny-1:
        jj = 0
    if (booli[ii,jj,kk] == 0 and not oldcell) and \
      ((tracking_variable[i,j,k,ibase] <= tracking_variable[ii,jj,kk,iup])\
      and (tracking_variable[i,j,k,iup] >= tracking_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j-1; kk=k;  #look south
    if jj<0:
        jj = ny-1
    if (booli[ii,jj,kk] == 0 and not oldcell) and \
       ((tracking_variable[i,j,k,ibase] <= tracking_variable[ii,jj,kk,iup])\
       and (tracking_variable[i,j,k,iup] >= tracking_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j; kk=min(k+1,nt-1);  #look forward
    if (booli[ii,jj,kk] == 0 and not oldcell) and \
      ((tracking_variable[i,j,k,ibase] <= tracking_variable[ii,jj,kk,iup])\
      and (tracking_variable[i,j,k,iup] >= tracking_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j; kk=max(k-1,0);  #look backward
    if (booli[ii,jj,kk] == 0 and not oldcell) and \
      ((tracking_variable[i,j,k,ibase] <= tracking_variable[ii,jj,kk,iup])\
      and (tracking_variable[i,j,k,iup] >= tracking_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell) 
#################################################################################################
def create_new_cell(variable,bool):                                # input the boolean and the variable, output is the cells tracked (i,j,t) based on boolean 
    global tracking_variable,booli,nx,ny,nt;
    nx = len(variable[:,0,0,0])
    ny = len(variable[0,:,0,0])
    nt = len(variable[0,0,:,0])
    cell_number = 0;
    booli=bool
    tracking_variable=variable;
    variable_cells = []
    for k in range(0,nt):
        for j in range(0,ny):
            for i in range(0,nx):
                if booli[i,j,k]==0: 
                    new_cell=cell(cell_number) 
                    identify_elements_in_cell(i,j,k,new_cell)
                    #while oldcell:
                    #    new_cell.nelements_local=0
                    #    test=test+1
                    #    bool=identify_elements_in_cell(oi,oj,ok,new_cell,bool)

                    if new_cell.nelements>=nminelems:
                        variable_cells.append(new_cell)
                        variable_cells[cell_number].id = cell_number
                        cell_number = cell_number + 1
                    else:
                        del new_cell;
    return variable_cells, cell_number;
##################################################################################################
def fill_parent_array(cells,nx,ny,nt):                                     #fills parent_array variable with id numbers of cells corresponding to each grid point 
    parent_array=np.zeros((nx,ny,nt))                             # fills base and up with values of base and up at those grid points
    base=np.zeros((nx,ny,nt))
    up=np.zeros((nx,ny,nt))
    for c in range(0,len(cells)):
        for n in range(0,cells[c].nelements):
            parent_array[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].id + 1
            base[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[ibase][n]
            up[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[iup][n]
    return parent_array,base,up;
#################################################################################################
def find_parent(cells,parent_cells,parent_array,base,up):
    lnewparent=False
    for n in range(0,len(cells)):
        for nn in range(0,cells[n].nelements):
            i = cells[n].location[0][nn]
            j = cells[n].location[1][nn]
            t = cells[n].location[2][nn]
            if parent_array[i,j,t] > 0:
                if base[i,j,t] <= cells[n].value[iup][cells[n].nelements-1] and up[i,j,t] >= cells[n].value[ibase][cells[n].nelements-1]:
                    lnewparent = True
                    for np in range(0,cells[n].nparents):
                        if cells[n].nparents>0 and (cells[n].parents[np].id == parent_array[i,j,t]-1):
                            lnewparent=False
                    if lnewparent:
                        cells[n].parents.append(parent_cells[int(parent_array[i,j,t]-1)])
                        parent_cells[int(parent_array[i,j,t]-1)].children.append(cells[n])                       
                        cells[n].nparents = cells[n].nparents + 1
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren = \
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren + 1
    return cells,parent_cells;
#################################################################################################
def splitcell(cells, parent_cells, parent_array):
    nlist = 0; nnewlist = 0; newlist=0; nendlist = 0; endlist = 0;
    for n in range(0,len(cells)):
        for nn in range(0,cells[n].nelements):
            i=cells[n].location[0][nn]; j=cells[n].location[1][nn]; t=cells[n].location[2][nn];

#################################################################################################
def run_tracking(tracked_param,param_threshold):
    [tracked_variable,x,y,t] = retrieve_variable(tracked_param,nc_path+nc_filename);
    bool = find_boolean(tracked_variable[:,:,:,ipath],param_threshold,t_start)
    [cells,cell_number] = create_new_cell(tracked_variable,bool);
    print(tracked_param,":",len(cells))
    return cells,cell_number,tracked_variable,x,y,t,bool;
##################################################################################################
def make_animation_cells(x,y,cells,nt,minimum_elements,p_c):
    fig, ax = pl.subplots()
    cell_plot=np.zeros((len(x),len(y),nt));
    cell_parent_plot=np.zeros((len(x),len(y),nt));
    levels=[]
    levels_reduced=[]
    count=0
    for i in range (0,len(cells)):
        if cells[i].nelements>minimum_elements:
            levels.append(i)
            if (count%4)==0:
                levels_reduced.append(i)
            count=count+1
            for n in range(0,cells[i].nelements):   
                if cells[i].nelements>20000:
                    cell_plot[cells[i].location[0][n],cells[i].location[1][n],cells[i].location[2][n]] = 25
                else: 
                    cell_plot[cells[i].location[0][n],cells[i].location[1][n],cells[i].location[2][n]] = cells[i].id
    if p_c=='p':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nparents>0:
                for npar in range(0,cells[i].nparents):
                    for n in range(0,cells[i].parents[npar].nelements):      
                        cell_parent_plot[cells[i].parents[npar].location[0][n],cells[i].parents[npar].location[1][n],(cells[i].parents[npar].location[2][n])] = cells[i].id
    elif p_c=='c':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nchildren>0:
                for nchild in range(0,cells[i].nchildren):
                    for n in range(0,cells[i].children[nchild].nelements):      
                        cell_parent_plot[cells[i].children[nchild].location[0][n],cells[i].children[nchild].location[1][n],(cells[i].children[nchild].location[2][n])] = cells[i].id
    if len(cells)>nmaxcells:
        levels=levels_reduced
    def animate(i):
        ax.clear()
        if p_c=='p':
            ax.contourf(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.tab20b)
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.tab20b,linestyles='solid',linewidth=1.5)
        elif p_c=='c':
            ax.contourf(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.flag)
            ax.contour(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.flag,linestyles='solid')
        elif p_c=='':
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.flag)
        return ax;
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=True)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
##################################################################################################
def make_animation_contour(x,y,variable,nt):
    fig, ax = pl.subplots()
    def animate(i):
        ax.clear()
        CS = ax.contourf(x,y,variable[:,:,i])
        ax.clabel(CS, inline=True, fontsize=10)
        return ax;
        
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=False)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
#################################################################################################
def main_fun():
    global rain,thermal,core,cloud;
    [rain,rain_ncells,rain_variable,x,y,t,rain_boolean]= run_tracking('qr',qr_threshold)
    nx = len(rain_variable[:,0,0,0]); ny = len(rain_variable[0,:,0,0]); nt = len(rain_variable[0,0,:,0]);

    [cloud,cloud_ncells,cloud_path,x,y,t,cloud_boolean] = run_tracking('ql',ql_threshold)
    [core,core_ncells,core_path,x,y,t,core_boolean] = run_tracking('bc',bc_threshold)
    [thermal,thermal_ncells,couvreux,x,y,t,thermal_boolean] = run_tracking('couvreux',couv_threshold)
    [parent_array,base,up] = fill_parent_array(cloud,nx,ny,nt)
    [rain,cloud] = find_parent(rain,cloud,parent_array,base,up)
    global ani1,ani2,ani3;
    ani1 = make_animation_cells(x,y,cloud,nt,50,'')
    cloud_bool = np.where(cloud_path[:,:,:,0]>ql_threshold,1,0)
    #ani2 = make_animation_contour(x,y,cloud_bool,nt)
    #ani3 = make_animation_cells(x,y,cloud,nt,500,'c')
    pl.figure()
    plot1=[]
    for i in range(0,len(cloud)):
        plot1.append(cloud[i].nelements)
    pl.plot(plot1)
    pl.close('all')
#################################################################################

nc_path='/home/girish/microhh/cases/rico_rgn/rico_moist_moresavefiles/'
nc_filename='cloudtrack_variables_1.nc'
ipath=0; iup=1; ibase=2
qr_threshold = 0.05; ql_threshold = 0.1; couv_threshold = 0.05; bc_threshold = 1;
nminelems=4;nmaxelems=250;nmaxcells=1500;
t_start = 0; t_plot=7;
sys.setrecursionlimit(20000)

#make_netcdffile_fromcross(24060,30000,60,50,nc_path,nc_filename,True)  
main_fun()



In [ ]:
ani1


In [ ]:
ani2

In [ ]:
ani3

In [ ]:
import numpy as np
import netCDF4 as nc
import xarray as xr
import matplotlib.pyplot as pl
import math
import scipy.io as sc
import netCDF4 as nc
import os, glob
import matplotlib.animation as manimation
from IPython.display import HTML
from matplotlib import rc
from matplotlib import cm
import sys

def make_netcdffile_fromcross(time_start, time_end, time_gap, x_spacing, path, output_name, del_files): #output netcdf file with variable across time steps from dump files
    float_type = 'f8'
    time_ind_total = int((time_end-time_start)/time_gap) + 1
    time = np.linspace(time_start,time_end,time_ind_total)
    main_variable=['qr','ql','couvreux','bc']
    attribute=['path','up','base']
    cross_section='.xy.'
    cross_section_length = 90
    filename = path+main_variable[0] + attribute[0] + cross_section + str(format(int(time[0]),'07d'))
    fid=open(filename,'rb')
    x_length = int(np.sqrt(len(np.fromfile(fid))))
    x=np.linspace(x_spacing,x_length*x_spacing,x_length)
    y=np.linspace(x_spacing,x_length*x_spacing,x_length)
    nvar=3
    fid.close()
    if os.path.exists(path+output_name):
        os.remove(path+output_name)
    nc_file = nc.Dataset(path+output_name, mode="w", datamodel="NETCDF4", clobber=False)
    nc_file.createDimension("x", x_length)
    nc_file.createDimension("y", x_length)
    nc_file.createDimension("t", time_ind_total)
    nc_file.createDimension("nvar",nvar)
    nc_x = nc_file.createVariable("x", float_type, ("x"))
    nc_y = nc_file.createVariable("y", float_type, ("y"))
    nc_t = nc_file.createVariable("t", float_type, ("t"))
    nc_nvar = nc_file.createVariable("nvar", int, ("nvar"))

    for j in range(0,len(main_variable)-1):
        var_name = main_variable[j]
        locals()[var_name] = np.zeros((x_length,x_length,time_ind_total,nvar))
        locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t","nvar"))  
        for k in range(0,len(attribute)):                  
            for i in range(0,time_ind_total):
                filename = path+main_variable[j] + attribute[k] + cross_section + str(format(int(time[i]),'07d'))
                fid=open(filename,'rb')
                var = np.fromfile(fid)
                locals()[var_name][:,:,i,k]=np.reshape(var,[x_length,x_length])
                fid.close()
        locals()['nc_'+var_name][:] = locals()[var_name][:]
    
    var_name = main_variable[3]
    locals()[var_name] = np.zeros((x_length,x_length,time_ind_total))
    locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t"))                  
    for i in range(0,time_ind_total):
        filename = path+main_variable[3] +attribute[0]+ cross_section + str(format(int(time[i]),'07d'))
        fid=open(filename,'rb')
        var = np.fromfile(fid)
        locals()[var_name][:,:,i]=np.reshape(var,[x_length,x_length])
        fid.close()
    locals()['nc_'+var_name][:] = locals()[var_name][:]




    nc_x [:] = x[:]
    nc_y [:] = y[:]
    nc_t [:] = time[:]
    nc_nvar [:]=nvar 
    nc_file.close()
    if del_files:
        #files = ["u", "v", "w", "thl", "time", "qr", "ql", "couv", "grid", "nr","qt","therm","bc"]
        files = ["path","up","base"]
        for file in os.listdir(path):
            for i in range(0,len(files)):
                if file.find(files[i])!=-1: 
                    os.remove(path+file)
                #rm u* v* w* thl* time* qr* ql* couv* grid* nr* qt* therm* 
##########################################################################################
def retrieve_variable(variable_name,netcdf_path): #open corresponding netcdf file and read data
    all_data=xr.open_dataset(netcdf_path)
    var=all_data[variable_name].values
    if variable_name=='bc':
        variable=np.zeros((len(var[:,0,0]),len(var[0,:,0]),len(var[0,0,:]),3))
        variable[:,:,:,0] = var
    else:
        variable=var
    x=all_data['x'].values
    y=all_data['y'].values
    t=all_data['t'].values
    return variable, x, y, t;    
##########################################################################################
def find_boolean(variable, threshold_criteria, i_tstart): #variable is f(i, j, t): --> outputs boolean -1 (unsatisfied) 0 (satisfied) 
    boolean = np.zeros(( len(variable[:,0,0]), len(variable[0,:,0]), len(variable[0,0,:])))
    boolean = -1
    boolean = np.where(variable>threshold_criteria,0,-1)
    if i_tstart>0:
        boolean[:,:,0:i_tstart-1] = -1
    return boolean;
##########################################################################################
class cell:
    def __init__(self, id):
        self.id = id
        self.value = [[],[],[]]
        self.location = [[],[],[]]
        self.nelements = 0
        self.nelements_local = 0
        self.nchildren = 0
        self.nparents = 0
        self.nsiblings = 0
        self.nsplitters = 0
        self.parents = []
        self.children = []

    def add_elements(self, i, j, k, var_values):
        self.location[0].append(i)
        self.location[1].append(j)
        self.location[2].append(k)
        self.value[0].append(var_values[0])
        self.value[1].append(var_values[1])
        self.value[2].append(var_values[2])
        self.nelements = self.nelements + 1
        self.nelements_local = self.nelements_local + 1
    def __del__(self):
        return
########################################################################################
def identify_elements_in_cell(variable,i,j,k,new_cell):  #input the ijk at which boolean is satisfied along with boolean and new cell created 
    nx = len(variable[:,0,0,0])                                  # outputs the cell with with added elements in it (location and value of it)
    ny = len(variable[0,:,0,0])
    nt = len(variable[0,0,:,0])
    global oldcell,oi,oj,ok
    new_cell.add_elements(i,j,k,variable[i,j,k,:])
    booli[i,j,k] = -2

    if (new_cell.nelements_local<=nmaxelems):
        oldcell=False
        
        ii=i-1; jj=j; kk=k; #look west
        if ii<0:
            ii = nx-1
        if (booli[ii,jj,kk] == 0) and \
        ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
        and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
            identify_elements_in_cell(variable,ii,jj,kk,new_cell)

        ii=i+1; jj=j; kk=k;  #look east
        if ii>nx-1:
            ii = 0
        if (booli[ii,jj,kk] == 0) and \
        ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
        and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
            identify_elements_in_cell(variable,ii,jj,kk,new_cell)

        ii=i; jj=j+1; kk=k;  #look north
        if jj>ny-1:
            jj = 0
        if (booli[ii,jj,kk] == 0) and \
        ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
        and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
            identify_elements_in_cell(variable,ii,jj,kk,new_cell)

        ii=i; jj=j-1; kk=k;  #look south
        if jj<0:
            jj = ny-1
        if (booli[ii,jj,kk] == 0) and \
        ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
        and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
            new_cell.add_elements(ii,jj,kk,variable[ii,jj,kk,:])
            identify_elements_in_cell(variable,ii,jj,kk,new_cell)

        ii=i; jj=j; kk=min(k+1,nt-1);  #look forward
        if (booli[ii,jj,kk] == 0) and \
        ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
        and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
            identify_elements_in_cell(variable,ii,jj,kk,new_cell)

        ii=i; jj=j; kk=max(k-1,0);  #look backward
        if (booli[ii,jj,kk] == 0) and \
        ((variable[i,j,k,ibase] <= variable[ii,jj,kk,iup])\
        and (variable[i,j,k,iup] >= variable[ii,jj,kk,ibase])) :
            identify_elements_in_cell(variable,ii,jj,kk,new_cell)
    else:
        oldcell = True
        oi=i;oj=j;ok=k;
    return
#################################################################################################
def create_new_cell(variable,bool):                                # input the boolean and the variable, output is the cells tracked (i,j,t) based on boolean 
    nx = len(variable[:,0,0,0])
    ny = len(variable[0,:,0,0])
    nt = len(variable[0,0,:,0])
    cell_number = 0;
    global booli;
    booli=bool;
    test=0; 
    variable_cells = []
    for k in range(0,nt):
        for j in range(0,ny):
            for i in range(0,nx):
                if booli[i,j,k]==0: 
                    new_cell=cell(cell_number) 
                    identify_elements_in_cell(variable,i,j,k,new_cell)
                    while oldcell:
                        test=test+1
                        new_cell.nelements_local = 0;
                        identify_elements_in_cell(variable,oi,oj,ok,new_cell)
                    if new_cell.nelements>=nminelems:
                        variable_cells.append(new_cell)
                        variable_cells[cell_number].id = cell_number
                        cell_number = cell_number + 1
                    else:
                        del new_cell;
    return variable_cells, cell_number;
##################################################################################################
def fill_parent_array(cells,nx,ny,nt):                                     #fills parent_array variable with id numbers of cells corresponding to each grid point 
    parent_array=np.zeros((nx,ny,nt))                             # fills base and up with values of base and up at those grid points
    base=np.zeros((nx,ny,nt))
    up=np.zeros((nx,ny,nt))
    for c in range(0,len(cells)):
        for n in range(0,cells[c].nelements):
            parent_array[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].id + 1
            base[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[ibase][n]
            up[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[iup][n]
    return parent_array,base,up;
#################################################################################################
def find_parent(cells,parent_cells,parent_array,base,up):
    lnewparent=False
    for n in range(0,len(cells)):
        for nn in range(0,cells[n].nelements):
            i = cells[n].location[0][nn]
            j = cells[n].location[1][nn]
            t = cells[n].location[2][nn]
            if parent_array[i,j,t] > 0:
                if base[i,j,t] <= cells[n].value[iup][cells[n].nelements-1] and up[i,j,t] >= cells[n].value[ibase][cells[n].nelements-1]:
                    lnewparent = True
                    for np in range(0,cells[n].nparents):
                        if cells[n].nparents>0 and (cells[n].parents[np].id == parent_array[i,j,t]-1):
                            lnewparent=False
                    if lnewparent:
                        cells[n].parents.append(parent_cells[int(parent_array[i,j,t]-1)])
                        parent_cells[int(parent_array[i,j,t]-1)].children.append(cells[n])                       
                        cells[n].nparents = cells[n].nparents + 1
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren = \
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren + 1
    return cells,parent_cells;
#################################################################################################
def splitcell(cells, parent_cells, parent_array):
    nlist = 0; nnewlist = 0; newlist=0; nendlist = 0; endlist = 0;
    for n in range(0,len(cells)):
        for nn in range(0,cells[n].nelements):
            i=cells[n].location[0][nn]; j=cells[n].location[1][nn]; t=cells[n].location[2][nn];

#################################################################################################
def run_tracking(tracked_param,param_threshold):
    [tracked_variable,x,y,t] = retrieve_variable(tracked_param,nc_path+nc_filename);
    bool = find_boolean(tracked_variable[:,:,:,ipath],param_threshold,t_start)
    [cells,cell_number] = create_new_cell(tracked_variable,bool);
    print(tracked_param)
    return cells,cell_number,tracked_variable,x,y,t,bool;
##################################################################################################
def make_animation_cells(x,y,cells,nt,minimum_elements,p_c):
    fig, ax = pl.subplots()
    cell_plot=np.zeros((len(x),len(y),nt));
    cell_parent_plot=np.zeros((len(x),len(y),nt));
    levels=[]
    levels_reduced=[]
    count=0
    for i in range (0,len(cells)):
        if cells[i].nelements>minimum_elements:
            levels.append(i)
            if (count%4)==0:
                levels_reduced.append(i)
            count=count+1
            for n in range(0,cells[i].nelements):   
                if cells[i].nelements>20000:
                    cell_plot[cells[i].location[0][n],cells[i].location[1][n],cells[i].location[2][n]] = 25
                else: 
                    cell_plot[cells[i].location[0][n],cells[i].location[1][n],cells[i].location[2][n]] = cells[i].id
    if p_c=='p':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nparents>0:
                for npar in range(0,cells[i].nparents):
                    for n in range(0,cells[i].parents[npar].nelements):      
                        cell_parent_plot[cells[i].parents[npar].location[0][n],cells[i].parents[npar].location[1][n],(cells[i].parents[npar].location[2][n])] = cells[i].id
    elif p_c=='c':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nchildren>0:
                for nchild in range(0,cells[i].nchildren):
                    for n in range(0,cells[i].children[nchild].nelements):      
                        cell_parent_plot[cells[i].children[nchild].location[0][n],cells[i].children[nchild].location[1][n],(cells[i].children[nchild].location[2][n])] = cells[i].id
    if len(cells)>nmaxcells:
        levels=levels_reduced
    def animate(i):
        ax.clear()
        if p_c=='p':
            ax.contourf(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.tab20b)
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.tab20b,linestyles='solid',linewidth=1.5)
        elif p_c=='c':
            ax.contourf(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.flag)
            ax.contour(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.flag,linestyles='solid')
        elif p_c=='':
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.flag)
        return ax;
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=True)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
##################################################################################################
def make_animation_contour(x,y,variable,nt):
    fig, ax = pl.subplots()
    def animate(i):
        ax.clear()
        CS = ax.contourf(x,y,variable[:,:,i])
        ax.clabel(CS, inline=True, fontsize=10)
        return ax;
        
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=False)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
#################################################################################################
def main_fun():
    global rain,thermal,core,cloud;
    [rain,rain_ncells,rain_variable,x,y,t,rain_boolean]= run_tracking('qr',qr_threshold)
    nx = len(rain_variable[:,0,0,0]); ny = len(rain_variable[0,:,0,0]); nt = len(rain_variable[0,0,:,0]);

    [cloud,cloud_ncells,cloud_path,x,y,t,cloud_boolean] = run_tracking('ql',ql_threshold)
    [core,core_ncells,core_path,x,y,t,core_boolean] = run_tracking('bc',bc_threshold)
    [thermal,thermal_ncells,couvreux,x,y,t,thermal_boolean] = run_tracking('couvreux',couv_threshold)
    [parent_array,base,up] = fill_parent_array(cloud,nx,ny,nt)
    [rain,cloud] = find_parent(rain,cloud,parent_array,base,up)
    global ani1,ani2,ani3;
    ani1 = make_animation_cells(x,y,cloud,nt,50,'')
    cloud_bool = np.where(cloud_path[:,:,:,0]>ql_threshold,1,0)
    #ani2 = make_animation_contour(x,y,cloud_bool,nt)
    #ani3 = make_animation_cells(x,y,cloud,nt,500,'c')
    pl.figure()
    plot1=[]
    for i in range(0,len(cloud)):
        plot1.append(cloud[i].nelements)
    pl.plot(plot1)
    pl.close('all')
#################################################################################

nc_path='/home/girish/microhh/cases/rico_rgn/rico_moist_moresavefiles/'
nc_filename='cloudtrack_variables_1.nc'
ipath=0; iup=1; ibase=2
qr_threshold = 0.01; ql_threshold = 0.05; couv_threshold = 0.05; bc_threshold = 0;
nminelems=4;nmaxelems=20000;nmaxcells=1500;
t_start = 0; t_plot=7;
sys.setrecursionlimit(20000)

#make_netcdffile_fromcross(24060,30000,60,50,nc_path,nc_filename,True)  
main_fun()



In [2]:
import numpy as np
import netCDF4 as nc
import xarray as xr
import matplotlib.pyplot as pl
import math
import scipy.io as sc
import netCDF4 as nc
import os, glob
import matplotlib.animation as manimation
from IPython.display import HTML
from matplotlib import rc
from matplotlib import cm
import sys

def make_netcdffile_fromcross(time_start, time_end, time_gap, x_spacing, path, output_name, del_files): #output netcdf file with variable across time steps from dump files
    float_type = 'f8'
    time_ind_total = int((time_end-time_start)/time_gap) + 1
    time = np.linspace(time_start,time_end,time_ind_total)
    main_variable=['qr','ql','couvreux','bc']
    attribute=['path','up','base']
    cross_section='.xy.'
    cross_section_length = 90
    filename = path+main_variable[0] + attribute[0] + cross_section + str(format(int(time[0]),'07d'))
    fid=open(filename,'rb')
    x_length = int(np.sqrt(len(np.fromfile(fid))))
    x=np.linspace(x_spacing,x_length*x_spacing,x_length)
    y=np.linspace(x_spacing,x_length*x_spacing,x_length)
    nvar=3
    fid.close()
    if os.path.exists(path+output_name):
        os.remove(path+output_name)
    nc_file = nc.Dataset(path+output_name, mode="w", datamodel="NETCDF4", clobber=False)
    nc_file.createDimension("x", x_length)
    nc_file.createDimension("y", x_length)
    nc_file.createDimension("t", time_ind_total)
    nc_file.createDimension("nvar",nvar)
    nc_x = nc_file.createVariable("x", float_type, ("x"))
    nc_y = nc_file.createVariable("y", float_type, ("y"))
    nc_t = nc_file.createVariable("t", float_type, ("t"))
    nc_nvar = nc_file.createVariable("nvar", int, ("nvar"))

    for j in range(0,len(main_variable)-1):
        var_name = main_variable[j]
        locals()[var_name] = np.zeros((x_length,x_length,time_ind_total,nvar))
        locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t","nvar"))  
        for k in range(0,len(attribute)):                  
            for i in range(0,time_ind_total):
                filename = path+main_variable[j] + attribute[k] + cross_section + str(format(int(time[i]),'07d'))
                fid=open(filename,'rb')
                var = np.fromfile(fid)
                locals()[var_name][:,:,i,k]=np.reshape(var,[x_length,x_length])
                fid.close()
        locals()['nc_'+var_name][:] = locals()[var_name][:]
    
    var_name = main_variable[3]
    locals()[var_name] = np.zeros((x_length,x_length,time_ind_total))
    locals()['nc_'+var_name] = nc_file.createVariable(var_name, float_type, ("x","y","t"))                  
    for i in range(0,time_ind_total):
        filename = path+main_variable[3] +attribute[0]+ cross_section + str(format(int(time[i]),'07d'))
        fid=open(filename,'rb')
        var = np.fromfile(fid)
        locals()[var_name][:,:,i]=np.reshape(var,[x_length,x_length])
        fid.close()
    locals()['nc_'+var_name][:] = locals()[var_name][:]




    nc_x [:] = x[:]
    nc_y [:] = y[:]
    nc_t [:] = time[:]
    nc_nvar [:]=nvar 
    nc_file.close()
    if del_files:
        #files = ["u", "v", "w", "thl", "time", "qr", "ql", "couv", "grid", "nr","qt","therm","bc"]
        files = ["path","up","base.xy"]
        for file in os.listdir(path):
            for i in range(0,len(files)):
                if file.find(files[i])!=-1: 
                    os.remove(path+file)
                #rm u* v* w* thl* time* qr* ql* couv* grid* nr* qt* therm* 
##########################################################################################
def retrieve_variable(variable_name,netcdf_path): #open corresponding netcdf file and read data
    all_data=xr.open_dataset(netcdf_path)
    var=all_data[variable_name].values
    if variable_name=='bc':
        variable=np.zeros((len(var[:,0,0]),len(var[0,:,0]),len(var[0,0,:]),3))
        variable[:,:,:,0] = var
    else:
        variable=var
    x=all_data['x'].values
    y=all_data['y'].values
    t=all_data['t'].values
    return variable, x, y, t;    
##########################################################################################
def find_boolean(variable, threshold_criteria, i_tstart): #variable is f(i, j, t): --> outputs boolean -1 (unsatisfied) 0 (satisfied) 
    boolean = np.zeros(( len(variable[:,0,0]), len(variable[0,:,0]), len(variable[0,0,:])))
    boolean = -1
    boolean = np.where(variable>threshold_criteria,0,-1)
    if i_tstart>0:
        boolean[:,:,0:i_tstart-1] = -1
    return boolean;
##########################################################################################
class cell:
    def __init__(self, id):
        self.id = id
        self.value = [[],[],[]]
        self.location = [[],[],[]]
        self.nelements = 0
        self.nelements_local = 0
        self.nchildren = 0
        self.nparents = 0
        self.nsiblings = 0
        self.nsplitters = 0
        self.parents = []
        self.children = []

    def add_elements(self, i, j, k, var_values):
        self.location[0].append(i)
        self.location[1].append(j)
        self.location[2].append(k)
        self.value[0].append(var_values[0])
        self.value[1].append(var_values[1])
        self.value[2].append(var_values[2])
        self.nelements = self.nelements + 1
        self.nelements_local = self.nelements_local + 1
    def __del__(self):
        return
########################################################################################
def identify_elements_in_cell(i,j,k,new_cell):  #input the ijk at which boolean is satisfied along with boolean and new cell created 

    global oldcell,oi,oj,ok,booli;
    new_cell.add_elements(i,j,k,cell_variable[i,j,k,:])
    booli[i,j,k] = -2

    ii=i-1; jj=j; kk=k; #look west
    if ii<0:
       ii = nx-1
    if (booli[ii,jj,kk] == 0) and \
      ((cell_variable[i,j,k,ibase] <= cell_variable[ii,jj,kk,iup])\
      and (cell_variable[i,j,k,iup] >= cell_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i+1; jj=j; kk=k;  #look east
    if ii>nx-1:
       ii = 0
    if (booli[ii,jj,kk] == 0) and \
      ((cell_variable[i,j,k,ibase] <= cell_variable[ii,jj,kk,iup])\
      and (cell_variable[i,j,k,iup] >= cell_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j+1; kk=k;  #look north
    if jj>ny-1:
        jj = 0
    if (booli[ii,jj,kk] == 0) and \
      ((cell_variable[i,j,k,ibase] <= cell_variable[ii,jj,kk,iup])\
      and (cell_variable[i,j,k,iup] >= cell_variable[ii,jj,kk,ibase])) :
        identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j-1; kk=k;  #look south
    if jj<0:
       jj = ny-1
    if (booli[ii,jj,kk] == 0) and \
      ((cell_variable[i,j,k,ibase] <= cell_variable[ii,jj,kk,iup])\
      and (cell_variable[i,j,k,iup] >= cell_variable[ii,jj,kk,ibase])) :
       identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j; kk=min(k+1,nt-1);  #look forward
    if (booli[ii,jj,kk] == 0) and \
      ((cell_variable[i,j,k,ibase] <= cell_variable[ii,jj,kk,iup])\
      and (cell_variable[i,j,k,iup] >= cell_variable[ii,jj,kk,ibase])) :
            if new_cell.nelements_local>nmaxelems:
                oldcell = True;
                oi.append(ii);oj.append(jj);ok.append(kk);
            else:
                identify_elements_in_cell(ii,jj,kk,new_cell)

    ii=i; jj=j; kk=max(k-1,0);  #look backward
    if (booli[ii,jj,kk] == 0) and \
      ((cell_variable[i,j,k,ibase] <= cell_variable[ii,jj,kk,iup])\
      and (cell_variable[i,j,k,iup] >= cell_variable[ii,jj,kk,ibase])) :
            identify_elements_in_cell(ii,jj,kk,new_cell)

#################################################################################################
def create_new_cell(variable,bool):                                # input the boolean and the variable, output is the cells tracked (i,j,t) based on boolean 
    cell_number = 0;
    global booli,cell_variable,nx,ny,nt,oldcell,flag,oi,oj,ok;
    nx = len(variable[:,0,0,0])
    ny = len(variable[0,:,0,0])
    nt = len(variable[0,0,:,0])
    booli=bool;cell_variable = variable;
    test=0; 
    variable_cells = []
    for k in range(0,nt):
        for j in range(0,ny):
            for i in range(0,nx):
                if booli[i,j,k]==0: 
                    oldcell=False;oi=[];oj=[];ok=[];
                    new_cell=cell(cell_number) 
                    identify_elements_in_cell(i,j,k,new_cell)
                    ii=oi;jj=oj;kk=ok;
                    while oldcell:
                        oldcell=False;oi=[];oj=[];ok=[];
                        test=test+1
                        new_cell.nelements_local = 0;
                        for n in range(0,len(ii)):
                            if new_cell.nelements_local<nmaxelems:
                                identify_elements_in_cell(ii[n],jj[n],kk[n],new_cell)
                            else:
                                oi.append(ii[n]);oj.append(jj[n]);ok.append(kk[n]);
                                oldcell=True;
                        ii=oi;jj=oj;kk=ok;              
                    if new_cell.nelements>=nminelems:
                        variable_cells.append(new_cell)
                        variable_cells[cell_number].id = cell_number
                        cell_number = cell_number + 1
                    else:
                        del new_cell;
    print(test)
    return variable_cells, cell_number;
##################################################################################################
def fill_parent_array(cells,nx,ny,nt):                                     #fills parent_array variable with id numbers of cells corresponding to each grid point 
    parent_array=np.zeros((nx,ny,nt))                             # fills base and up with values of base and up at those grid points
    base=np.zeros((nx,ny,nt))
    up=np.zeros((nx,ny,nt))
    for c in range(0,len(cells)):
        for n in range(0,cells[c].nelements):
            parent_array[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].id + 1
            base[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[ibase][n]
            up[cells[c].location[0][n],cells[c].location[1][n],cells[c].location[2][n]]\
                        = cells[c].value[iup][n]
    return parent_array,base,up;
#################################################################################################
def find_parent(cells,parent_cells,parent_array,base,up):
    lnewparent=False
    for n in range(0,len(cells)):
        for nn in range(0,cells[n].nelements):
            i = cells[n].location[0][nn]
            j = cells[n].location[1][nn]
            t = cells[n].location[2][nn]
            if parent_array[i,j,t] > 0:
                if base[i,j,t] <= cells[n].value[iup][cells[n].nelements-1] and up[i,j,t] >= cells[n].value[ibase][cells[n].nelements-1]:
                    lnewparent = True
                    for np in range(0,cells[n].nparents):
                        if cells[n].nparents>0 and (cells[n].parents[np].id == parent_array[i,j,t]-1):
                            lnewparent=False
                    if lnewparent:
                        cells[n].parents.append(parent_cells[int(parent_array[i,j,t]-1)])
                        parent_cells[int(parent_array[i,j,t]-1)].children.append(cells[n])                       
                        cells[n].nparents = cells[n].nparents + 1
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren = \
                        parent_cells[int(parent_array[i,j,t]-1)].nchildren + 1
    return cells,parent_cells;
#################################################################################################
def splitcell(cells, parent_cells, parent_array):
    nlist = 0; nnewlist = 0; newlist=0; nendlist = 0; endlist = 0;
    for n in range(0,len(cells)):
        for nn in range(0,cells[n].nelements):
            i=cells[n].location[0][nn]; j=cells[n].location[1][nn]; t=cells[n].location[2][nn];
            if parent_array[i,j,t]!=0:
                a=0;

#################################################################################################
def run_tracking(tracked_param,param_threshold):
    [tracked_variable,x,y,t] = retrieve_variable(tracked_param,nc_path+nc_filename);
    bool = find_boolean(tracked_variable[:,:,:,ipath],param_threshold,t_start)
    [cells,cell_number] = create_new_cell(tracked_variable,bool);
    print(tracked_param,":",len(cells))
    return cells,cell_number,tracked_variable,x,y,t,bool;
##################################################################################################
def make_animation_cells(x,y,cells,nt,minimum_elements,p_c):
    fig, ax = pl.subplots()
    cell_plot=np.zeros((len(x),len(y),nt));
    cell_parent_plot=np.zeros((len(x),len(y),nt));
    cell_children_plot=np.zeros((len(x),len(y),nt));
    levels=[]
    levels_reduced=[]
    count=0
    for i in range (0,len(cells)):
        if cells[i].nelements>minimum_elements:
            levels.append(cells[i].id)
            if (count%4)==0:
                levels_reduced.append(i)
            count=count+1
            for n in range(0,cells[i].nelements):      
                    cell_plot[cells[i].location[0][n],cells[i].location[1][n],cells[i].location[2][n]] = cells[i].id
    if p_c=='p' or p_c=='c_p':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nparents>0:
                for npar in range(0,cells[i].nparents):
                    for n in range(0,cells[i].parents[npar].nelements):      
                        cell_parent_plot[cells[i].parents[npar].location[0][n],cells[i].parents[npar].location[1][n],(cells[i].parents[npar].location[2][n])] = cells[i].id
    if p_c=='c'or p_c=='c_p':
        for i in range (0,len(cells)):
            if cells[i].nelements>minimum_elements and cells[i].nchildren>0:
                for nchild in range(0,cells[i].nchildren):
                    for n in range(0,cells[i].children[nchild].nelements):      
                        cell_children_plot[cells[i].children[nchild].location[0][n],cells[i].children[nchild].location[1][n],(cells[i].children[nchild].location[2][n])] = cells[i].id
    if count>nmaxcells:
        levels=levels_reduced
    def animate(i):
        ax.clear()
        if p_c=='p':
            ax.contourf(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.tab20b)
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.tab20b,linestyles='solid',linewidth=1.5)
        elif p_c=='c':
            ax.contourf(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.tab20b)
            ax.contour(x,y,cell_children_plot[:,:,i],levels=levels,cmap=cm.tab20b,linestyles='solid')
        elif p_c=='':
            ax.contour(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.flag)
        elif p_c=='c_p':
            ax.contourf(x,y,cell_plot[:,:,i],levels=levels,cmap=cm.tab20b)
            ax.contour(x,y,cell_children_plot[:,:,i],levels=levels,cmap=cm.tab20b,linestyles='solid')
            ax.contour(x,y,cell_parent_plot[:,:,i],levels=levels,cmap=cm.tab20b,linestyles='dashed')   
        return ax;
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=True)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
##################################################################################################
def make_animation_contour(x,y,variable,nt):
    fig, ax = pl.subplots()
    def animate(i):
        ax.clear()
        CS = ax.contour(x,y,variable[:,:,i])
        ax.clabel(CS, inline=True, fontsize=10)
        return ax;
        
    ani = manimation.FuncAnimation(fig,animate,frames=nt,repeat=False)
    pl.show()
    HTML(ani.to_jshtml())
    pl.rcParams["animation.html"] = "jshtml"
    return ani
#################################################################################################
def main_fun():
    global rain,thermal,core,cloud;
    [rain,rain_ncells,rain_variable,x,y,t,rain_boolean]= run_tracking('qr',qr_threshold)
    nx = len(rain_variable[:,0,0,0]); ny = len(rain_variable[0,:,0,0]); nt = len(rain_variable[0,0,:,0]);

    [cloud,cloud_ncells,cloud_path,x,y,t,cloud_boolean] = run_tracking('ql',ql_threshold)
    [core,core_ncells,core_path,x,y,t,core_boolean] = run_tracking('bc',bc_threshold)
    [thermal,thermal_ncells,couvreux,x,y,t,thermal_boolean] = run_tracking('couvreux',couv_threshold)
    [parent_array,base,up] = fill_parent_array(cloud,nx,ny,nt)
    [rain,cloud] = find_parent(rain,cloud,parent_array,base,up)
    del parent_array,base,up;
    [parent_array,base,up] = fill_parent_array(thermal,nx,ny,nt)
    [cloud,thermal] = find_parent(cloud,thermal,parent_array,base,up);

    global ani1,ani2,ani3;
    ani1 = make_animation_cells(x,y,cloud,nt,1000,'c_p')
    #cloud_bool = np.where(cloud_path[:,:,:,0]>ql_threshold,1,0)
    #ani2 = make_animation_contour(x,y,cloud_bool,nt)
    #ani3 = make_animation_cells(x,y,cloud,nt,500,'c')
    pl.figure()
    plot1=[]
    for i in range(0,len(cloud)):
        plot1.append(cloud[i].nelements)
    pl.plot(plot1)
#################################################################################

nc_path='/home/girish/microhh/cases/rico_rgn/rico_largerdomain/'
nc_filename='cloudtrack_variables_1024.nc'
ipath=0; iup=1; ibase=2
qr_threshold = 0.01; ql_threshold = 0.05; couv_threshold = 0.05; bc_threshold = 1;
nminelems=5;nmaxelems=1000;nmaxcells=1500;
x_spacing=25;
t_start = 0; t_plot=7;
sys.setrecursionlimit(20000)

#make_netcdffile_fromcross(24060,36000,60,x_spacing,nc_path,nc_filename,True)  
main_fun()


5069
qr : 2206


RecursionError: maximum recursion depth exceeded while calling a Python object

In [2]:
ani1